# Target Problem

The project proposes to use a deep reinforcement learning framework to learn a profitable stock trading strategy, with the goal to optimize the cumulative return and Alpha. It would select S&P500 Index with the top 20 market capitalization stocks as our trading stock pool. The input to the algorithm is the market trend for these stocks in the last month, remaining balance, and current portfolio. The model agent output is a series of trading actions among stocks. The available trading
action options are: sell, buy and hold. The market data in the most recent months will be used to feed
the model performance evaluation.

The algorithm is trained using Deep Reinforcement Learning (DRL) algorithms and the components of the reinforcement learning environment are:

* Action: The action space describes the allowed actions that the agent interacts with the
environment. Normally, a ∈ A includes three actions: a ∈ {−1, 0, 1}, where −1, 0, 1 represent
selling, holding, and buying one stock. Also, an action can be carried upon multiple shares. We use
an action space {−k, ..., −1, 0, 1, ..., k}, where k denotes the number of shares. For example, "Buy
10 shares of AAPL" or "Sell 10 shares of AAPL" are 10 or −10, respectively

* Reward function: r(s, a, s′) is the incentive mechanism for an agent to learn a better action. The change of the portfolio value when action a is taken at state s and arriving at new state s',  i.e., r(s, a, s′) = v′ − v, where v′ and v represent the portfolio
values at state s′ and s, respectively

* State: The state space describes the observations that the agent receives from the environment. Just as a human trader needs to analyze various information before executing a trade, so
our trading agent observes many different features to better learn in an interactive environment.

* Environment: SP500 top 20 companies


The data of the single stock that we will be using for this case study is obtained from Yahoo Finance API. The data contains Open-High-Low-Close price and volume.


## Environment Setup

### Import Packages

In [1]:
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
from datetime import datetime
from datetime import timedelta

%matplotlib inline
from rl.config import config
from rl.marketdata.yahoodownloader import YahooDownloader
from rl.preprocessing.preprocessors import FeatureEngineer
from rl.preprocessing.data import data_split
from rl.env.env_stocktrading import StockTradingEnv
from rl.model.models import DRLAgent
from rl.trade.backtest import backtest_stats, backtest_plot, get_daily_return, get_baseline

from pprint import pprint

import itertools

D:\InstalledSoftware\anaconda3\envs\py37-python-notebook\lib\site-packages\pyfolio\pos.py:26: UserWarning: Module "zipline.assets" not found; multipliers will not be applied to position notionals.
  warnings.warn(


### Cache Folders

In [2]:
import os
if not os.path.exists("./" + config.DATA_SAVE_DIR):
    os.makedirs("./" + config.DATA_SAVE_DIR)
if not os.path.exists("./" + config.TRAINED_MODEL_DIR):
    os.makedirs("./" + config.TRAINED_MODEL_DIR)
if not os.path.exists("./" + config.TENSORBOARD_LOG_DIR):
    os.makedirs("./" + config.TENSORBOARD_LOG_DIR)
if not os.path.exists("./" + config.RESULTS_DIR):
    os.makedirs("./" + config.RESULTS_DIR)

### Fetch Data

In [3]:
# from config.py start_date is a string
start_date = config.START_DATE
# from config.py end_date is a string
end_date = config.END_DATE
# from config.py split_date is a string
split_date = config.SPLIT_DATE
# config target ticker
target_ticker = config.SP500_20_TICKER
# config tech_indicator_list
tech_indicator_list = config.TECHNICAL_INDICATORS_LIST
print("training period: {}-{}, testing period: {}-{}\n".format(start_date, split_date, split_date, end_date))
print("target ticker list:\n {}\n".format(target_ticker))
print("tech_indicator_list:\n {}\n".format(tech_indicator_list))

training period: 2000-01-01-2019-01-01, testing period: 2019-01-01-2021-01-01

target ticker list:
 ['AAPL', 'MSFT', 'AMZN', 'BRK-B', 'JPM', 'JNJ', 'UNH', 'HD', 'PG', 'NVDA', 'DIS', 'BAC', 'CMCSA', 'XOM', 'VZ', 'T', 'ADBE', 'PFE', 'CSCO', 'INTC']

tech_indicator_list:
 ['macd', 'boll_ub', 'boll_lb', 'rsi_10', 'rsi_20', 'cci_10', 'cci_20', 'dx_30', 'close_20_sma', 'close_60_sma', 'close_120_sma', 'close_20_ema', 'close_60_ema', 'close_120_ema']



In [4]:
df = YahooDownloader(start_date = start_date,
                     end_date = end_date,
                     ticker_list = target_ticker).fetch_data()

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

In [5]:
df.shape

(105680, 8)

In [6]:
df.sort_values(['date','tic'],ignore_index=True).head()

date       open       high        low      close       volume    tic  \
0  2000-01-03   0.936384   1.004464   0.907924   0.859423  535796800.0   AAPL   
1  2000-01-03  16.812500  16.875000  16.062500  16.274673    7384400.0   ADBE   
2  2000-01-03  81.500000  89.562500  79.046875  89.375000   16117600.0   AMZN   
3  2000-01-03  25.125000  25.125000  24.000000  13.952057   13705800.0    BAC   
4  2000-01-03  36.500000  36.580002  34.820000  35.299999     875000.0  BRK-B   

   day  
0    0  
1    0  
2    0  
3    0  
4    0

## Data Preprocessing
Data preprocessing is a crucial step for training a high quality machine learning model. We need to check for missing data and do feature engineering in order to convert the data into a model-ready state.
* Add technical indicators. In practical trading, various information needs to be taken into account, for example the historical stock prices, current holding shares, technical indicators, etc. In this article, we demonstrate two trend-following technical indicators: MACD and RSI.
* Add turbulence index. Risk-aversion reflects whether an investor will choose to preserve the capital. It also influences one's trading strategy when facing different market volatility level. To control the risk in a worst-case scenario, such as financial crisis of 2007–2008, FinRL employs the financial turbulence index that measures extreme asset price fluctuation.

### Feature Engineering

In [7]:
fe = FeatureEngineer(
                    use_technical_indicator=True,
                    tech_indicator_list = tech_indicator_list,
                    use_turbulence=True,
                    user_defined_feature = False)

processed = fe.preprocess_data(df)

Successfully added technical indicators
Successfully added turbulence index


In [8]:
print(processed.shape)
processed.head()

(105680, 23)


date       open       high        low      close       volume    tic  \
0  2000-01-03   0.936384   1.004464   0.907924   0.859423  535796800.0   AAPL   
1  2000-01-03  16.812500  16.875000  16.062500  16.274673    7384400.0   ADBE   
2  2000-01-03  81.500000  89.562500  79.046875  89.375000   16117600.0   AMZN   
3  2000-01-03  25.125000  25.125000  24.000000  13.952057   13705800.0    BAC   
4  2000-01-03  36.500000  36.580002  34.820000  35.299999     875000.0  BRK-B   

   day  macd   boll_ub  ...     cci_10     cci_20  dx_30  close_20_sma  \
0    0   0.0  0.925665  ... -66.666667 -66.666667  100.0      0.859423   
1    0   0.0  0.925665  ... -66.666667 -66.666667  100.0     16.274673   
2    0   0.0  0.925665  ... -66.666667 -66.666667  100.0     89.375000   
3    0   0.0  0.925665  ... -66.666667 -66.666667  100.0     13.952057   
4    0   0.0  0.925665  ... -66.666667 -66.666667  100.0     35.299999   

   close_60_sma  close_120_sma  close_20_ema  close_60_ema  close_120_ema  \
0      0.859423       0.859423      0.859423      0.859423       0.859423   
1     16.274673      16.274673     16.274673     16.274673      16.274673   
2     89.375000      89.375000     89.375000     89.375000      89.375000   
3     13.952057      13.952057     13.952057     13.952057      13.952057   
4     35.299999      35.299999     35.299999     35.299999      35.299999   

   turbulence  
0         0.0  
1         0.0  
2         0.0  
3         0.0  
4         0.0  

[5 rows x 23 columns]

### Data display

In [9]:
list_ticker = processed["tic"].unique().tolist()
print(list_ticker)
list_date = list(pd.date_range(processed['date'].min(),processed['date'].max()).astype(str))
combination = list(itertools.product(list_date,list_ticker))
processed_full = pd.DataFrame(combination,columns=["date","tic"]).merge(processed,on=["date","tic"],how="left")
processed_full = processed_full[processed_full['date'].isin(processed['date'])]
processed_full = processed_full.sort_values(['date','tic'])
processed_full = processed_full.fillna(0)

['AAPL', 'ADBE', 'AMZN', 'BAC', 'BRK-B', 'CMCSA', 'CSCO', 'DIS', 'HD', 'INTC', 'JNJ', 'JPM', 'MSFT', 'NVDA', 'PFE', 'PG', 'T', 'UNH', 'VZ', 'XOM']


In [10]:
processed_full.sort_values(['date','tic'],ignore_index=True).head(10)

date    tic       open       high        low      close       volume  \
0  2000-01-03   AAPL   0.936384   1.004464   0.907924   0.859423  535796800.0   
1  2000-01-03   ADBE  16.812500  16.875000  16.062500  16.274673    7384400.0   
2  2000-01-03   AMZN  81.500000  89.562500  79.046875  89.375000   16117600.0   
3  2000-01-03    BAC  25.125000  25.125000  24.000000  13.952057   13705800.0   
4  2000-01-03  BRK-B  36.500000  36.580002  34.820000  35.299999     875000.0   
5  2000-01-03  CMCSA  16.145832  16.333332  15.062500  12.189544    2333700.0   
6  2000-01-03   CSCO  54.968750  55.125000  51.781250  40.118656   53076000.0   
7  2000-01-03    DIS  28.855125  29.533344  28.361876  23.115248    8402230.0   
8  2000-01-03     HD  68.625000  69.187500  63.812500  42.563168   12030800.0   
9  2000-01-03   INTC  41.632812  43.687500  41.625000  27.002798   57710200.0   

   day  macd   boll_ub  ...     cci_10     cci_20  dx_30  close_20_sma  \
0  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0      0.859423   
1  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     16.274673   
2  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     89.375000   
3  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     13.952057   
4  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     35.299999   
5  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     12.189544   
6  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     40.118656   
7  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     23.115248   
8  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     42.563168   
9  0.0   0.0  0.925665  ... -66.666667 -66.666667  100.0     27.002798   

   close_60_sma  close_120_sma  close_20_ema  close_60_ema  close_120_ema  \
0      0.859423       0.859423      0.859423      0.859423       0.859423   
1     16.274673      16.274673     16.274673     16.274673      16.274673   
2     89.375000      89.375000     89.375000     89.375000      89.375000   
3     13.952057      13.952057     13.952057     13.952057      13.952057   
4     35.299999      35.299999     35.299999     35.299999      35.299999   
5     12.189544      12.189544     12.189544     12.189544      12.189544   
6     40.118656      40.118656     40.118656     40.118656      40.118656   
7     23.115248      23.115248     23.115248     23.115248      23.115248   
8     42.563168      42.563168     42.563168     42.563168      42.563168   
9     27.002798      27.002798     27.002798     27.002798      27.002798   

   turbulence  
0         0.0  
1         0.0  
2         0.0  
3         0.0  
4         0.0  
5         0.0  
6         0.0  
7         0.0  
8         0.0  
9         0.0  

[10 rows x 23 columns]

### Data Split

In [11]:
train = data_split(processed_full, start_date, split_date)
evaluate = data_split(processed_full, split_date, end_date)
print(train.shape)
print(evaluate.shape)

(95580, 23)
(10100, 23)


## RL Environment
Considering the stochastic and interactive nature of the automated stock trading tasks, a financial task is modeled as a **Markov Decision Process (MDP)** problem. The training process involves observing stock price change, taking an action and reward's calculation to have the agent adjusting its strategy accordingly. By interacting with the environment, the trading agent will derive a trading strategy with the maximized rewards as time proceeds.

Our trading environments, based on OpenAI Gym framework, simulate live stock markets with real market data according to the principle of time-driven simulation.

The action space describes the allowed actions that the agent interacts with the environment. Normally, action a includes three actions: {-1, 0, 1}, where -1, 0, 1 represent selling, holding, and buying one share. Also, an action can be carried upon multiple shares. We use an action space {-k,…,-1, 0, 1, …, k}, where k denotes the number of shares to buy and -k denotes the number of shares to sell. For example, "Buy 10 shares of AAPL" or "Sell 10 shares of AAPL" are 10 or -10, respectively. The continuous action space needs to be normalized to [-1, 1], since the policy is defined on a Gaussian distribution, which needs to be normalized and symmetric.

In [14]:
stock_dimension = len(processed_full.tic.unique())
state_space = 1 + 2*stock_dimension + len(tech_indicator_list)*stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")

Stock Dimension: 20, State Space: 321


In [15]:
def predict_train(model_name, env_params, model_kwargs, total_timesteps):
    train = data_split(processed_full, start_date, split_date)
    e_train_gym = StockTradingEnv(df = train, **env_params)
    # Environment for training
    env_train, _ = e_train_gym.get_sb_env()
    print(type(env_train))
    # Train model
    agent = DRLAgent(env = env_train)
    if model_name == 'a2c' or model_name == 'ddpg':
        model = agent.get_model(model_name)
    else:
        model = agent.get_model(model_name, model_kwargs = model_kwargs)  
    
    trained_model = agent.train_model(
        model=model, 
        tb_log_name=model_name,
        total_timesteps=total_timesteps)

    df_value, df_actions = dict(), dict()
    df_value['training_'+model_name], df_actions['training_'+model_name] = DRLAgent.DRL_prediction(trained_model, e_train_gym)
    
    return df_value, df_actions    

In [16]:
def rolling_prediction_month(model_name, dataset, predict_time_period, env_params, model_kwargs, total_timesteps):
    # Split data
    period = datetime.strptime(predict_time_period, "%Y-%m") #2019-01
    monthFirstDate = period.replace(day=1)
    if monthFirstDate.month == 12:
        nextMonthFirstDate = monthFirstDate.replace(year=monthFirstDate.year+1, month=1)
    else:
        nextMonthFirstDate = monthFirstDate.replace(month=monthFirstDate.month+1)
    train = data_split(processed_full, start_date, monthFirstDate.strftime("%Y-%m-%d"))
    evaluate = data_split(processed_full, monthFirstDate.strftime("%Y-%m-%d"), nextMonthFirstDate.strftime("%Y-%m-%d"))
    e_train_gym = StockTradingEnv(df = train, **env_params)
    e_evaluation_gym = StockTradingEnv(df=evaluate, **env_params)
    # Environment for training
    env_train, _ = e_train_gym.get_sb_env()
    print(type(env_train))
    # Train model
    agent = DRLAgent(env = env_train)
    if model_name == 'a2c' or model_name == 'ddpg':
        model = agent.get_model(model_name)
    else:
        model = agent.get_model(model_name, model_kwargs = model_kwargs)  
    
    trained_model = agent.train_model(
        model=model, 
        tb_log_name=model_name,
        total_timesteps=total_timesteps)

    df_value, df_actions = dict(), dict()
    #df_value['training_'+model_name], df_actions['training_'+model_name] = DRLAgent.DRL_prediction(trained_model, e_train_gym)
    df_value['evaluation_'+model_name], df_actions['evaluation_'+model_name] = DRLAgent.DRL_prediction(trained_model, e_evaluation_gym)
    
    return df_value, df_actions


In [17]:
def rolling_prediction_quarter(model_name, dataset, predict_time_period, env_params, model_kwargs, total_timesteps):
    # Split data
    period = datetime.strptime(predict_time_period, "%Y-%m") #2019-01
    monthFirstDate = period.replace(day=1)
    if monthFirstDate.month >= 10:
        nextQuarterFirstDate = monthFirstDate.replace(year=monthFirstDate.year+1, month=(monthFirstDate.month + 3)%12)
    else:
        nextQuarterFirstDate = monthFirstDate.replace(month=monthFirstDate.month+3)
    train = data_split(processed_full, start_date, monthFirstDate.strftime("%Y-%m-%d"))
    evaluate = data_split(processed_full, monthFirstDate.strftime("%Y-%m-%d"), nextQuarterFirstDate.strftime("%Y-%m-%d"))
    e_train_gym = StockTradingEnv(df = train, **env_params)
    e_evaluation_gym = StockTradingEnv(df=evaluate, **env_params)
    # Environment for training
    env_train, _ = e_train_gym.get_sb_env()
    print(type(env_train))
    # Train model
    agent = DRLAgent(env = env_train)
    if model_name == 'a2c' or model_name == 'ddpg':
        model = agent.get_model(model_name)
    else:
        model = agent.get_model(model_name, model_kwargs = model_kwargs)  
    
    trained_model = agent.train_model(
        model=model, 
        tb_log_name=model_name,
        total_timesteps=total_timesteps)

    df_value, df_actions = dict(), dict()
    #df_value['training_'+model_name], df_actions['training_'+model_name] = DRLAgent.DRL_prediction(trained_model, e_train_gym)
    df_value['evaluation_'+model_name], df_actions['evaluation_'+model_name] = DRLAgent.DRL_prediction(trained_model, e_evaluation_gym)
    
    return df_value, df_actions


In [18]:
def predict_test_month(model_name, months, start_date, env_params, model_kwargs, total_timesteps):
    start_datetime = datetime.strptime(start_date, "%Y-%m-%d")
    df_value_result, df_actions_result = dict(), dict()

    for i in range(months):
        predict_time_period = start_datetime.replace(year=start_datetime.year+int(i/12), month=start_datetime.month+i%12).strftime("%Y-%m")

        df_value, df_actions = rolling_prediction_month(model_name, processed_full, predict_time_period, env_params, model_kwargs, total_timesteps)
        
        for key in df_value:
            if key not in df_value_result:
                df_value_result[key] = df_value[key]
            else:
                df_value_result[key] = pd.concat([df_value_result[key], df_value[key]])
        for key in df_actions:
            if key not in df_actions_result:
                df_actions_result[key] = df_actions[key]
            else:
                df_actions_result[key] = pd.concat([df_actions_result[key], df_actions[key]])
        env_params["initial_amount"] = df_value['evaluation_'+model_name].iloc[-1].account_value
  
    return df_value_result, df_actions_result

In [19]:
def predict_test_quarter(model_name, quarters, start_date, env_params, model_kwargs, total_timesteps):
    start_datetime = datetime.strptime(start_date, "%Y-%m-%d") #2019-01-01
    df_value_result, df_actions_result = dict(), dict()

    for i in range(quarters):
        predict_time_period = start_datetime.replace(year=start_datetime.year+int(i/4), month=start_datetime.month+3*(i%4)).strftime("%Y-%m")

        df_value, df_actions = rolling_prediction_quarter(model_name, processed_full, predict_time_period, env_params, model_kwargs, total_timesteps)
        
        for key in df_value:
            if key not in df_value_result:
                df_value_result[key] = df_value[key]
            else:
                df_value_result[key] = pd.concat([df_value_result[key], df_value[key]])
        for key in df_actions:
            if key not in df_actions_result:
                df_actions_result[key] = df_actions[key]
            else:
                df_actions_result[key] = pd.concat([df_actions_result[key], df_actions[key]])
        env_params["initial_amount"] = df_value['evaluation_'+model_name].iloc[-1].account_value
  
    return df_value_result, df_actions_result

In [20]:
def main_function(model_name, env_params, model_kwargs, total_timesteps):
    df_value, df_actions = dict(), dict()
    df_value_train, df_actions_train = predict_train(model_name, env_params, model_kwargs, total_timesteps)
    df_value.update(df_value_train)
    df_actions.update(df_actions_train)
    df_value_test, df_actions_test = predict_test_quarter(model_name, 8, split_date, env_params, model_kwargs, total_timesteps)
    #df_value_test, df_actions_test = predict_test_month(model_name, 24, split_date, env_params, model_kwargs, total_timesteps)
    df_value.update(df_value_test)
    df_actions.update(df_actions_test)
    return df_value, df_actions

In [23]:
env_params = {
    "hmax": 100, 
    "initial_amount": 1000000, 
    "buy_cost_pct": 0.001,
    "sell_cost_pct": 0.001,
    "state_space": state_space, 
    "stock_dim": stock_dimension, 
    "tech_indicator_list": tech_indicator_list, 
    "action_space": stock_dimension, 
    "reward_scaling": 1e-6
}
A2C_PARAMS = {
    "n_steps": 5, 
    "ent_coef": 0.005, 
    "learning_rate": 0.0001}
PPO_PARAMS = {
    "n_steps": 2048,
    "ent_coef": 0.005,
    "learning_rate": 0.0001,
    "batch_size": 128,
}
DDPG_PARAMS = {
    "batch_size": 128, 
    "buffer_size": 100000, 
    "learning_rate": 0.0005
}
TD3_PARAMS = {
    "batch_size": 128, 
    "buffer_size": 100000, 
    "learning_rate": 0.0005
}
SAC_PARAMS = {
    "batch_size": 128,
    "buffer_size": 100000,
    "learning_rate": 0.0001,
    "learning_starts": 100,
    "ent_coef": "auto_0.1"
}
total_timesteps = 100000

In [24]:
df_value, df_actions = dict(), dict()

In [25]:
df_value_a2c, df_actions_a2c = main_function("a2c", env_params, A2C_PARAMS, total_timesteps=100000)
df_value.update(df_value_a2c)
df_actions.update(df_actions_a2c)

[1000000, 0.859423041343689, 16.274673461914062, 89.375, 13.952056884765625, 35.29999923706055, 12.189543724060059, 40.118656158447266, 23.11524772644043, 42.563167572021484, 27.002798080444336, 26.6447696685791, 25.863813400268555, 36.93210220336914, 3.585430383682251, 14.565584182739258, 30.248369216918945, 15.941187858581543, 5.632353782653809, 20.573511123657227, 20.461938858032227, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.720722899924667, 0.720722899924667, 0.720722899924667, 0.72072289992

Logging to tensorboard_log/a2c\a2c_11
------------------------------------
| time/                 |          |
|    fps                | 54       |
|    iterations         | 100      |
|    time_elapsed       | 9        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -29.6    |
|    explained_variance | 0        |
|    learning_rate      | 0.0007   |
|    n_updates          | 99       |
|    policy_loss        | -0.109   |
|    std                | 1.06     |
|    value_loss         | 2.87e-05 |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 64       |
|    iterations         | 200      |
|    time_elapsed       | 15       |
|    total_timesteps    | 1000     |
| train/                |          |
|    entropy_loss       | -30.4    |
|    explained_variance | 1.19e-07 |
|    learning_rate      | 0.0007   |
|    n_updates          | 199      |


------------------------------------
| environment/          |          |
|    portfolio_value    | 1.83e+06 |
|    total_cost         | 1.09e+05 |
|    total_reward       | 8.34e+05 |
|    total_reward_pct   | 83.4     |
|    total_trades       | 73389    |
| time/                 |          |
|    fps                | 81       |
|    iterations         | 1000     |
|    time_elapsed       | 61       |
|    total_timesteps    | 5000     |
| train/                |          |
|    entropy_loss       | -34.9    |
|    explained_variance | -274     |
|    learning_rate      | 0.0007   |
|    n_updates          | 999      |
|    policy_loss        | 4.16     |
|    std                | 1.38     |
|    value_loss         | 0.0395   |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 81       |
|    iterations         | 1100     |
|    time_elapsed       | 67       |
|    total_timesteps    | 5500     |
|

------------------------------------
| environment/          |          |
|    portfolio_value    | 2.01e+06 |
|    total_cost         | 5.48e+04 |
|    total_reward       | 1.01e+06 |
|    total_reward_pct   | 101      |
|    total_trades       | 66599    |
| time/                 |          |
|    fps                | 86       |
|    iterations         | 2000     |
|    time_elapsed       | 116      |
|    total_timesteps    | 10000    |
| train/                |          |
|    entropy_loss       | -41.1    |
|    explained_variance | 0        |
|    learning_rate      | 0.0007   |
|    n_updates          | 1999     |
|    policy_loss        | 1.9      |
|    std                | 1.89     |
|    value_loss         | 0.00276  |
------------------------------------
-------------------------------------
| time/                 |           |
|    fps                | 86        |
|    iterations         | 2100      |
|    time_elapsed       | 120       |
|    total_timesteps    | 10500  

------------------------------------
| environment/          |          |
|    portfolio_value    | 8.68e+06 |
|    total_cost         | 3.4e+04  |
|    total_reward       | 7.68e+06 |
|    total_reward_pct   | 768      |
|    total_trades       | 59352    |
| time/                 |          |
|    fps                | 89       |
|    iterations         | 2900     |
|    time_elapsed       | 162      |
|    total_timesteps    | 14500    |
| train/                |          |
|    entropy_loss       | -46.2    |
|    explained_variance | -45.5    |
|    learning_rate      | 0.0007   |
|    n_updates          | 2899     |
|    policy_loss        | 3.79     |
|    std                | 2.44     |
|    value_loss         | 0.0179   |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 89       |
|    iterations         | 3000     |
|    time_elapsed       | 168      |
|    total_timesteps    | 15000    |
|

...

------------------------------------
| environment/          |          |
|    portfolio_value    | 1.03e+07 |
|    total_cost         | 5.9e+05  |
|    total_reward       | 8.91e+06 |
|    total_reward_pct   | 640      |
|    total_trades       | 99292    |
| time/                 |          |
|    fps                | 109      |
|    iterations         | 15700    |
|    time_elapsed       | 715      |
|    total_timesteps    | 78500    |
| train/                |          |
|    entropy_loss       | -105     |
|    explained_variance | 0        |
|    learning_rate      | 0.0007   |
|    n_updates          | 15699    |
|    policy_loss        | -2.79    |
|    std                | 45.9     |
|    value_loss         | 0.000937 |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 109      |
|    iterations         | 15800    |
|    time_elapsed       | 719      |
|    total_timesteps    | 79000    |
|

-------------------------------------
| environment/          |           |
|    portfolio_value    | 9.93e+05  |
|    total_cost         | 2.65e+05  |
|    total_reward       | -3.99e+05 |
|    total_reward_pct   | -28.7     |
|    total_trades       | 89935     |
| time/                 |           |
|    fps                | 109       |
|    iterations         | 16800     |
|    time_elapsed       | 765       |
|    total_timesteps    | 84000     |
| train/                |           |
|    entropy_loss       | -111      |
|    explained_variance | 0         |
|    learning_rate      | 0.0007    |
|    n_updates          | 16799     |
|    policy_loss        | 1.15      |
|    std                | 63.9      |
|    value_loss         | 0.000129  |
-------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 109      |
|    iterations         | 16900    |
|    time_elapsed       | 770      |
|    total_timest

------------------------------------
| environment/          |          |
|    portfolio_value    | 1.58e+07 |
|    total_cost         | 6.12e+05 |
|    total_reward       | 1.44e+07 |
|    total_reward_pct   | 1.03e+03 |
|    total_trades       | 100319   |
| time/                 |          |
|    fps                | 109      |
|    iterations         | 17800    |
|    time_elapsed       | 811      |
|    total_timesteps    | 89000    |
| train/                |          |
|    entropy_loss       | -116     |
|    explained_variance | -74.5    |
|    learning_rate      | 0.0007   |
|    n_updates          | 17799    |
|    policy_loss        | 1.58     |
|    std                | 80.6     |
|    value_loss         | 0.0185   |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 109      |
|    iterations         | 17900    |
|    time_elapsed       | 815      |
|    total_timesteps    | 89500    |
|

------------------------------------
| environment/          |          |
|    portfolio_value    | 6.32e+06 |
|    total_cost         | 5.74e+05 |
|    total_reward       | 4.93e+06 |
|    total_reward_pct   | 354      |
|    total_trades       | 97125    |
| time/                 |          |
|    fps                | 109      |
|    iterations         | 18800    |
|    time_elapsed       | 856      |
|    total_timesteps    | 94000    |
| train/                |          |
|    entropy_loss       | -121     |
|    explained_variance | 0        |
|    learning_rate      | 0.0007   |
|    n_updates          | 18799    |
|    policy_loss        | -1.57    |
|    std                | 102      |
|    value_loss         | 0.000261 |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 109      |
|    iterations         | 18900    |
|    time_elapsed       | 861      |
|    total_timesteps    | 94500    |
|

------------------------------------
| environment/          |          |
|    portfolio_value    | 1.62e+07 |
|    total_cost         | 6.12e+05 |
|    total_reward       | 1.49e+07 |
|    total_reward_pct   | 1.07e+03 |
|    total_trades       | 100659   |
| time/                 |          |
|    fps                | 109      |
|    iterations         | 19900    |
|    time_elapsed       | 906      |
|    total_timesteps    | 99500    |
| train/                |          |
|    entropy_loss       | -126     |
|    explained_variance | 0        |
|    learning_rate      | 0.0007   |
|    n_updates          | 19899    |
|    policy_loss        | -3.36    |
|    std                | 131      |
|    value_loss         | 0.000833 |
------------------------------------
------------------------------------
| time/                 |          |
|    fps                | 109      |
|    iterations         | 20000    |
|    time_elapsed       | 911      |
|    total_timesteps    | 100000   |
|

In [26]:
df_value_ppo, df_actions_ppo = main_function("ppo", env_params, PPO_PARAMS, total_timesteps=100000)
df_value.update(df_value_ppo)
df_actions.update(df_actions_ppo)

[1344640.3196638909, 0.859423041343689, 16.274673461914062, 89.375, 13.952056884765625, 35.29999923706055, 12.189543724060059, 40.118656158447266, 23.11524772644043, 42.563167572021484, 27.002798080444336, 26.6447696685791, 25.863813400268555, 36.93210220336914, 3.585430383682251, 14.565584182739258, 30.248369216918945, 15.941187858581543, 5.632353782653809, 20.573511123657227, 20.461938858032227, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.720722899924667, 0.720722899924667, 0.720722899924667, 0.

-----------------------------
| time/              |      |
|    fps             | 124  |
|    iterations      | 1    |
|    time_elapsed    | 16   |
|    total_timesteps | 2048 |
-----------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 123         |
|    iterations           | 2           |
|    time_elapsed         | 33          |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.006376017 |
|    clip_fraction        | 0.0831      |
|    clip_range           | 0.2         |
|    entropy_loss         | -28.4       |
|    explained_variance   | 0.776       |
|    learning_rate        | 0.0001      |
|    loss                 | -0.153      |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.00604    |
|    std                  | 1           |
|    value_loss           | 0.00337     |
----------------------------------

[1344640.3196638909, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.599542983784

[1344640.3196638909, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.599542983784

-----------------------------------------
| environment/            |             |
|    portfolio_value      | 7.3e+06     |
|    total_cost           | 2.52e+05    |
|    total_reward         | 5.96e+06    |
|    total_reward_pct     | 443         |
|    total_trades         | 92048       |
| time/                   |             |
|    fps                  | 109         |
|    iterations           | 10          |
|    time_elapsed         | 186         |
|    total_timesteps      | 20480       |
| train/                  |             |
|    approx_kl            | 0.007833547 |
|    clip_fraction        | 0.0878      |
|    clip_range           | 0.2         |
|    entropy_loss         | -28.4       |
|    explained_variance   | -1.52       |
|    learning_rate        | 0.0001      |
|    loss                 | -0.152      |
|    n_updates            | 90          |
|    policy_gradient_loss | -0.0139     |
|    std                  | 1           |
|    value_loss           | 0.0167

...

-----------------------------------------
| environment/            |             |
|    portfolio_value      | 9.88e+06    |
|    total_cost           | 3.49e+05    |
|    total_reward         | 8.46e+06    |
|    total_reward_pct     | 597         |
|    total_trades         | 99367       |
| time/                   |             |
|    fps                  | 113         |
|    iterations           | 36          |
|    time_elapsed         | 649         |
|    total_timesteps      | 73728       |
| train/                  |             |
|    approx_kl            | 0.015944727 |
|    clip_fraction        | 0.121       |
|    clip_range           | 0.2         |
|    entropy_loss         | -28.6       |
|    explained_variance   | -1.05       |
|    learning_rate        | 0.0001      |
|    loss                 | -0.146      |
|    n_updates            | 350         |
|    policy_gradient_loss | -0.0116     |
|    std                  | 1.01        |
|    value_loss           | 0.0072

-----------------------------------------
| environment/            |             |
|    portfolio_value      | 1.51e+07    |
|    total_cost           | 3.72e+05    |
|    total_reward         | 1.37e+07    |
|    total_reward_pct     | 968         |
|    total_trades         | 98299       |
| time/                   |             |
|    fps                  | 113         |
|    iterations           | 39          |
|    time_elapsed         | 703         |
|    total_timesteps      | 79872       |
| train/                  |             |
|    approx_kl            | 0.007074467 |
|    clip_fraction        | 0.0971      |
|    clip_range           | 0.2         |
|    entropy_loss         | -28.6       |
|    explained_variance   | 0.0209      |
|    learning_rate        | 0.0001      |
|    loss                 | -0.161      |
|    n_updates            | 380         |
|    policy_gradient_loss | -0.015      |
|    std                  | 1.01        |
|    value_loss           | 0.0237

-----------------------------------------
| time/                   |             |
|    fps                  | 113         |
|    iterations           | 42          |
|    time_elapsed         | 757         |
|    total_timesteps      | 86016       |
| train/                  |             |
|    approx_kl            | 0.014547687 |
|    clip_fraction        | 0.127       |
|    clip_range           | 0.2         |
|    entropy_loss         | -28.6       |
|    explained_variance   | 0.225       |
|    learning_rate        | 0.0001      |
|    loss                 | -0.143      |
|    n_updates            | 410         |
|    policy_gradient_loss | -0.0162     |
|    std                  | 1.01        |
|    value_loss           | 0.0471      |
-----------------------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 113         |
|    iterations           | 43          |
|    time_elapsed         | 775   

-----------------------------------------
| time/                   |             |
|    fps                  | 113         |
|    iterations           | 45          |
|    time_elapsed         | 811         |
|    total_timesteps      | 92160       |
| train/                  |             |
|    approx_kl            | 0.009028841 |
|    clip_fraction        | 0.116       |
|    clip_range           | 0.2         |
|    entropy_loss         | -28.6       |
|    explained_variance   | 0.273       |
|    learning_rate        | 0.0001      |
|    loss                 | -0.147      |
|    n_updates            | 440         |
|    policy_gradient_loss | -0.0153     |
|    std                  | 1.01        |
|    value_loss           | 0.0293      |
-----------------------------------------
[1416627.52092334, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.7831687

------------------------------------------
| time/                   |              |
|    fps                  | 113          |
|    iterations           | 48           |
|    time_elapsed         | 865          |
|    total_timesteps      | 98304        |
| train/                  |              |
|    approx_kl            | 0.0099581955 |
|    clip_fraction        | 0.128        |
|    clip_range           | 0.2          |
|    entropy_loss         | -28.6        |
|    explained_variance   | 0.494        |
|    learning_rate        | 0.0001       |
|    loss                 | -0.166       |
|    n_updates            | 470          |
|    policy_gradient_loss | -0.015       |
|    std                  | 1.01         |
|    value_loss           | 0.00589      |
------------------------------------------
day: 5219, episode: 20
begin_total_asset: 1416627.52
end_total_asset: 21215389.65
total_reward: 19798762.13
total_cost: 364841.09
total_trades: 97555
Sharpe: 0.709
[1416627.52092334, 

In [27]:
df_value_ddpg, df_actions_ddpg = main_function("ddpg", env_params, DDPG_PARAMS, total_timesteps=100000)
df_value.update(df_value_ddpg)
df_actions.update(df_actions_ddpg)

[1381128.606066386, 0.859423041343689, 16.274673461914062, 89.375, 13.952056884765625, 35.29999923706055, 12.189543724060059, 40.118656158447266, 23.11524772644043, 42.563167572021484, 27.002798080444336, 26.6447696685791, 25.863813400268555, 36.93210220336914, 3.585430383682251, 14.565584182739258, 30.248369216918945, 15.941187858581543, 5.632353782653809, 20.573511123657227, 20.461938858032227, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.720722899924667, 0.720722899924667, 0.720722899924667, 0.7

[1381128.606066386, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[1381128.606066386, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[1381128.606066386, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[1381128.606066386, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

...

[2316931.4945522742, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09762889148660747, -1.538717541838217, 124.75066379762033, 516.3452954675917, 3424.4058012080236, 26.499112487032153, 223.82616156910208, 46.54627183291475, 40.8864

[2316931.4945522742, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09762889148660747, -1.538717541838217, 124.75066379762033, 516.3452954675917, 3424.4058012080236, 26.499112487032153, 223.82616156910208, 46.54627183291475, 40.8864

[2316931.4945522742, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09762889148660747, -1.538717541838217, 124.75066379762033, 516.3452954675917, 3424.4058012080236, 26.499112487032153, 223.82616156910208, 46.54627183291475, 40.8864

day: 5219, episode: 20
begin_total_asset: 2316931.49
end_total_asset: 37857935.03
total_reward: 35541003.54
total_cost: 2314.62
total_trades: 57335
Sharpe: 0.706
[2316931.4945522742, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09

[2316931.4945522742, 116.21749114990234, 499.510009765625, 3221.260009765625, 23.83234977722168, 212.02000427246094, 45.78659439086914, 38.21390151977539, 123.30999755859375, 274.3949890136719, 51.23431396484375, 144.4952392578125, 94.83293914794922, 210.9312286376953, 544.2313232421875, 33.45813751220703, 136.76589965820312, 27.027074813842773, 310.84332275390625, 57.581138610839844, 31.352582931518555, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.3162659026794188, 3.366134143650811, -19.75288215695491, -0.4186219596480143, 0.015138443054610207, 0.6414959537462579, -0.9747507763204268, -1.445068682956773, -0.6417142710326402, 0.26292107530031217, -0.531493784443569, -1.1642559396602508, -0.8381830712603744, 11.634598589196003, -0.23064029449312073, 0.7364955415837926, -0.33542145646494603, -0.7242032530563733, 0.08141772221854637, -1.6093227555390826, 120.72073113445377, 506.02128111467425, 3345.89976136453, 26.38511277912158, 223.0417729826497, 46.66342824522005, 40

In [28]:
df_value_td3, df_actions_td3 = main_function("td3", env_params, TD3_PARAMS, total_timesteps=100000)
df_value.update(df_value_td3)
df_actions.update(df_actions_td3)

[2396078.3918556003, 0.859423041343689, 16.274673461914062, 89.375, 13.952056884765625, 35.29999923706055, 12.189543724060059, 40.118656158447266, 23.11524772644043, 42.563167572021484, 27.002798080444336, 26.6447696685791, 25.863813400268555, 36.93210220336914, 3.585430383682251, 14.565584182739258, 30.248369216918945, 15.941187858581543, 5.632353782653809, 20.573511123657227, 20.461938858032227, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.720722899924667, 0.720722899924667, 0.720722899924667, 0.

[2396078.3918556003, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.599542983784

[2396078.3918556003, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.599542983784

[2396078.3918556003, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.599542983784

[2396078.3918556003, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.599542983784

...

[3461962.7733582812, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09762889148660747, -1.538717541838217, 124.75066379762033, 516.3452954675917, 3424.4058012080236, 26.499112487032153, 223.82616156910208, 46.54627183291475, 40.8864

[3461962.7733582812, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09762889148660747, -1.538717541838217, 124.75066379762033, 516.3452954675917, 3424.4058012080236, 26.499112487032153, 223.82616156910208, 46.54627183291475, 40.8864

[3461962.7733582812, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09762889148660747, -1.538717541838217, 124.75066379762033, 516.3452954675917, 3424.4058012080236, 26.499112487032153, 223.82616156910208, 46.54627183291475, 40.8864

day: 5219, episode: 20
begin_total_asset: 3461962.77
end_total_asset: 39942028.13
total_reward: 36480065.36
total_cost: 3458.50
total_trades: 88394
Sharpe: 0.652
[3461962.7733582812, 115.24229431152344, 490.42999267578125, 3148.72998046875, 23.822460174560547, 212.94000244140625, 45.609127044677734, 38.4404296875, 124.08000183105469, 274.48394775390625, 50.78316879272461, 146.0253143310547, 94.14836120605469, 208.81654357910156, 540.8734130859375, 33.76171112060547, 136.52032470703125, 27.04604721069336, 309.5525817871094, 57.6198844909668, 32.48820495605469, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.6520127833327081, 2.200447835811133, -30.52401975363273, -0.43892786784970994, 0.1271073967621419, 0.6408533764616138, -1.0380700287613536, -1.2922447955760958, -1.0320438950207063, 0.1278568856186908, -0.5949573236522383, -1.324438748408184, -1.3540465220062856, 9.889791023103271, -0.24867907586695992, 0.6648001235918173, -0.3579625669967541, -1.5978102358906199, 0.09

[3461962.7733582812, 116.21749114990234, 499.510009765625, 3221.260009765625, 23.83234977722168, 212.02000427246094, 45.78659439086914, 38.21390151977539, 123.30999755859375, 274.3949890136719, 51.23431396484375, 144.4952392578125, 94.83293914794922, 210.9312286376953, 544.2313232421875, 33.45813751220703, 136.76589965820312, 27.027074813842773, 310.84332275390625, 57.581138610839844, 31.352582931518555, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -0.3162659026794188, 3.366134143650811, -19.75288215695491, -0.4186219596480143, 0.015138443054610207, 0.6414959537462579, -0.9747507763204268, -1.445068682956773, -0.6417142710326402, 0.26292107530031217, -0.531493784443569, -1.1642559396602508, -0.8381830712603744, 11.634598589196003, -0.23064029449312073, 0.7364955415837926, -0.33542145646494603, -0.7242032530563733, 0.08141772221854637, -1.6093227555390826, 120.72073113445377, 506.02128111467425, 3345.89976136453, 26.38511277912158, 223.0417729826497, 46.66342824522005, 40

In [ ]:
df_value_sac, df_actions_sac = main_function("sac", env_params, SAC_PARAMS, total_timesteps=100000)
df_value.update(df_value_sac)
df_actions.update(df_actions_sac)

[3585471.025682727, 0.859423041343689, 16.274673461914062, 89.375, 13.952056884765625, 35.29999923706055, 12.189543724060059, 40.118656158447266, 23.11524772644043, 42.563167572021484, 27.002798080444336, 26.6447696685791, 25.863813400268555, 36.93210220336914, 3.585430383682251, 14.565584182739258, 30.248369216918945, 15.941187858581543, 5.632353782653809, 20.573511123657227, 20.461938858032227, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.925665153969376, 0.720722899924667, 0.720722899924667, 0.720722899924667, 0.7

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

...

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

day: 4778, episode: 10
begin_total_asset: 3585471.03
end_total_asset: 13113237.73
total_reward: 9527766.70
total_cost: 5354.55
total_trades: 38832
Sharpe: 0.453
[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

[3585471.025682727, 38.39591979980469, 226.24000549316406, 1501.969970703125, 23.346698760986328, 204.17999267578125, 32.51496124267578, 40.123985290527344, 108.32612609863281, 162.39141845703125, 44.13541793823242, 120.67992401123047, 90.1629638671875, 98.58563232421875, 132.7157745361328, 37.58075714111328, 86.1761703491211, 24.279356002807617, 240.15750122070312, 50.585201263427734, 58.40364074707031, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -2.141041777965299, -5.676368887152876, -53.443770397858316, -0.7670631267137757, -3.2557177528346415, -0.8954391581344154, -0.9799449674846201, -1.8656878145195321, -2.2328399684980695, -0.32983955379442875, -4.076795703828779, -2.889179649527293, -1.9850592357367844, -12.202282769826184, -0.31164924659512394, -0.15894413380489425, -0.5432299344854066, -6.482025623390342, -0.7203707316276251, -2.482863766377193, 44.89222937062556, 262.20470153717605, 1797.9009431978748, 26.367951753238582, 218.04005191465728, 37.5995429837843

### Evaluation
Backtesting plays a key role in evaluating the performance of a trading strategy. Automated backtesting tool is preferred because it reduces the human error. We usually use the Quantopian pyfolio package to backtest our trading strategies. It is easy to use and consists of various individual plots that provide a comprehensive image of the performance of a trading strategy.

In [ ]:
training_backtesting_list=['training_a2c', 'training_ppo', 'training_ddpg', 'training_td3', 'training_sac']
evaluation_backtesting_list=['evaluation_a2c', 'evaluation_ppo', 'evaluation_ddpg', 'evaluation_td3', 'evaluation_sac']

In [ ]:
local_time = datetime.now().strftime('%Y%m%d-%Hh%M')

def backtest(df_value, model_name):
    print("\n{} performance backtest:\n".format(model_name))
    perf_stats = backtest_stats(account_value=df_value)
    perf_stats = pd.DataFrame(perf_stats)
    perf_stats.to_csv("./"+config.RESULTS_DIR+"/perf_stats_"+model_name+"_"+local_time+'.csv')
    return perf_stats

perf_stats_all = dict()

print("================Training Period Perf================")
for model_name in training_backtesting_list:
    perf_stats = backtest(df_value[model_name], model_name)
    perf_stats_all[model_name] = perf_stats
print()
print("================Evaluation Period Perf================")
for model_name in evaluation_backtesting_list:
    perf_stats = backtest(df_value[model_name], model_name)
    perf_stats_all[model_name] = perf_stats

In [ ]:
# get baseline stats
print("baseline performance backtest:")
training_baseline_df = get_baseline(ticker="SPY", start=start_date,end=split_date)
evaluation_baseline_df = get_baseline(ticker="SPY", start=split_date,end=end_date)

print()
print("================Training Period Perf================")
stats = backtest_stats(training_baseline_df, value_col_name='close')
print()
print("================Evaluation Period Perf================")
stats = backtest_stats(evaluation_baseline_df, value_col_name='close')

### Backtesting Plot

### Training Performance

In [ ]:
%matplotlib inline
backtest_plot(df_value['training_a2c'], baseline_ticker = 'SPY', baseline_start = start_date, baseline_end = split_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['training_ppo'], baseline_ticker = 'SPY', baseline_start = start_date, baseline_end = split_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['training_sac'], baseline_ticker = 'SPY', baseline_start = start_date, baseline_end = split_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['training_ddpg'], baseline_ticker = 'SPY', baseline_start = start_date, baseline_end = split_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['training_td3'], baseline_ticker = 'SPY', baseline_start = start_date, baseline_end = split_date)

### Evaluation Performance

In [ ]:
%matplotlib inline
backtest_plot(df_value['evaluation_a2c'], baseline_ticker = 'SPY', baseline_start = split_date, baseline_end = end_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['evaluation_ppo'], baseline_ticker = 'SPY', baseline_start = split_date, baseline_end = end_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['evaluation_sac'], baseline_ticker = 'SPY', baseline_start = split_date, baseline_end = end_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['evaluation_ddpg'], baseline_ticker = 'SPY', baseline_start = split_date, baseline_end = end_date)

In [ ]:
%matplotlib inline
backtest_plot(df_value['evaluation_td3'], baseline_ticker = 'SPY', baseline_start = split_date, baseline_end = end_date)